## Dataset

In [1]:
import warnings
warnings.filterwarnings('ignore')

import sys
sys.path.append('/home/rupali/Documents/Master Thesis/jenga')

import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

from jenga.basis import Dataset

In [2]:
dataset = Dataset("thoracic_surgery") ## hill-valley ## thoracic_surgery ## cleve ## acute-inflammations

all_data = dataset.all_data
attribute_names = dataset.attribute_names
attribute_types = dataset.attribute_types

categorical_columns = dataset.categorical_columns
numerical_columns = dataset.numerical_columns

print(f"Found {len(categorical_columns)} categorical and {len(numerical_columns)} numeric features \n")

Dataset: thoracic_surgery
Found 13 categorical and 3 numeric features 



### Get training and test sets

In [3]:
train_data, train_labels, test_data, test_labels = dataset.get_train_test_data(0.3)

In [ ]:
########################################

In [4]:
## use categorical columns as strings
def cat_cols_to_str(df):
    for col in df.columns:
        if pd.api.types.is_categorical_dtype(df[col]):
            df[col] = df[col].astype(str)

    return df

In [5]:
### if we don't convert the categorical columns to str, the swapping corruption doesn't let us assign new values to the column: "Cannot setitem on a Categorical with a new category, set the categories first"
train_data = cat_cols_to_str(train_data)
test_data = cat_cols_to_str(test_data)

In [ ]:
########################################

## Workaround to get the data when OpenML decided not to work :D

In [ ]:
train_dat = pd.read_csv("/home/rupali/Downloads/Hill_Valley_without_noise_Training.data", sep=",")
train_data = train_dat.loc[:, train_dat.columns != 'class']
train_labels = train_dat["class"]

In [ ]:
test_dat = pd.read_csv("/home/rupali/Downloads/Hill_Valley_without_noise_Testing.data", sep=",")
test_data = test_dat.loc[:, test_dat.columns != 'class']
test_labels = test_dat["class"]

In [ ]:
categorical_columns = []
numerical_columns = []

for col in train_data.columns:
    if pd.api.types.is_categorical_dtype(train_data[col]):
        categorical_columns.append(col)
    elif pd.api.types.is_numeric_dtype(train_data[col]):
        numerical_columns.append(col)

print(f"Found {len(categorical_columns)} categorical and {len(numerical_columns)} numeric features \n")

## Defined Model

In [6]:
from sklearn.linear_model import SGDClassifier

learner = SGDClassifier(loss='log')
param_grid = {
    'learner__max_iter': [500, 1000, 5000],
    'learner__penalty': ['l2', 'l1', 'elasticnet'], 
    'learner__alpha': [0.0001, 0.001, 0.01, 0.1]
}

## Corruptions using PPP

In [7]:
from jenga.corruptions.generic import MissingValues, SwappedValues, CategoricalShift
from jenga.corruptions.numerical import Scaling, GaussianNoise

corruptions = [MissingValues, Scaling, CategoricalShift, GaussianNoise]#, SwappedValues]
fraction = 0.5
num_repetitions = 5

In [8]:
from jenga.cleaning.ppp import PipelinePerformancePrediction

ppp = PipelinePerformancePrediction(train_data, train_labels, test_data, test_labels, categorical_columns, numerical_columns, learner, param_grid)
ppp_model = ppp.fit_ppp(train_data)

## generate corrpted data
for _ in range(num_repetitions):
    df_corrupted, perturbations, cols_perturbed, summary_col_corrupt = ppp.get_corrupted(test_data, corruptions, fraction, num_repetitions)

Fitting 5 folds for each of 36 candidates, totalling 180 fits


/home/rupali/.local/lib/python3.8/site-packages/sklearn/feature_extraction/image.py:167: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  dtype=np.int):
/home/rupali/.local/lib/python3.8/site-packages/sklearn/ensemble/_gb.py:33: DeprecationWarning: `np.bool` is a deprecated alias for the builtin `bool`. To silence this warning, use `bool` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.bool_` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devd


Generating corrupted training data on 141 rows... 

	perturbation: MissingValues: {'column': 'AGE', 'fraction': 0.5, 'sampling': 'MCAR', 'na_value': nan}
	perturbation: Scaling: {'column': 'PRE4', 'fraction': 0.5, 'sampling': 'MAR'}
	perturbation: CategoricalShift: {'column': 'PRE14', 'fraction': 0.5, 'sampling': 'MCAR'}
	perturbation: GaussianNoise: {'column': 'PRE4', 'fraction': 0.5, 'sampling': 'MNAR'}

Generating corrupted training data on 141 rows... 

	perturbation: MissingValues: {'column': 'PRE25', 'fraction': 0.5, 'sampling': 'MAR', 'na_value': nan}
	perturbation: Scaling: {'column': 'AGE', 'fraction': 0.5, 'sampling': 'MCAR'}
	perturbation: CategoricalShift: {'column': 'PRE30', 'fraction': 0.5, 'sampling': 'MNAR'}
	perturbation: GaussianNoise: {'column': 'PRE5', 'fraction': 0.5, 'sampling': 'MNAR'}

Generating corrupted training data on 141 rows... 

	perturbation: MissingValues: {'column': 'PRE6', 'fraction': 0.5, 'sampling': 'MCAR', 'na_value': nan}
	perturbation: Scaling:

[Parallel(n_jobs=-1)]: Done 180 out of 180 | elapsed:    3.4s finished
/home/rupali/.local/lib/python3.8/site-packages/sklearn/model_selection/_search.py:818: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  dtype=np.int)


In [ ]:
train_data["PRE9"].unique()

In [ ]:
df_corrupted["PRE9"].unique()

## Autogluon model and Corruptions

In [ ]:
from jenga.corruptions.generic import MissingValues, SwappedValues, CategoricalShift
from jenga.corruptions.numerical import Scaling, GaussianNoise

corruptions = [MissingValues, Scaling, GaussianNoise, CategoricalShift]
fraction = 0.5
num_repetitions = 5

In [ ]:
from jenga.cleaning.ppp import PipelinePerformancePrediction

ppp = PipelinePerformancePrediction(train_data, train_labels, test_data, test_labels, categorical_columns, numerical_columns)
ppp_model = ppp.fit_ppp(train_data)
train_data = train_data.loc[:, train_data.columns != 'class']

## generate corrpted data
for _ in range(num_repetitions):
    df_corrupted, perturbations, cols_perturbed, summary_col_corrupt = ppp.get_corrupted(test_data, corruptions, fraction, num_repetitions)

## Cleaning

### PPP Cleaning

In [9]:
from jenga.cleaning.outlier_detection import NoOutlierDetection, PyODKNNOutlierDetection, PyODIsolationForestOutlierDetection, PyODPCAOutlierDetection, PyODCBLOFOutlierDetection, PyODSOSOutlierDetection, SklearnOutlierDetection
from jenga.cleaning.imputation import MeanModeImputation, SklearnImputation, DatawigImputation

cleaners = []
for od in [NoOutlierDetection, PyODKNNOutlierDetection, PyODIsolationForestOutlierDetection, PyODPCAOutlierDetection, PyODCBLOFOutlierDetection, PyODSOSOutlierDetection, SklearnOutlierDetection]:
    for imp in [MeanModeImputation, SklearnImputation, DatawigImputation]:
        cleaners.append((od, imp))

/home/rupali/.local/lib/python3.8/site-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [10]:
from jenga.cleaning.clean import Clean

categorical_precision_threshold=0.85
numerical_std_error_threshold=0.9

clean = Clean(train_data, df_corrupted, categorical_columns, numerical_columns, categorical_precision_threshold, numerical_std_error_threshold, ppp, ppp_model, cleaners)
df_outliers, df_cleaned, corrupted_score_ppp, best_cleaning_score, cleaner_scores_ppp, summary_cleaners = clean(train_data, test_data, df_corrupted, cols_perturbed)

/home/rupali/.local/lib/python3.8/site-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
/home/rupali/.local/lib/python3.8/site-packages/sklearn/linear_model/_base.py:295: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  indices = (scores > 0).astype(np.int)
/home/rupali/.local/li


Applying cleaners... 

PPP score no cleaning: {'roc_auc_score': 0.6543162719633308, 'classification_report': {'F': {'precision': 0.8467153284671532, 'recall': 0.9747899159663865, 'f1-score': 0.90625, 'support': 119}, 'T': {'precision': 0.25, 'recall': 0.045454545454545456, 'f1-score': 0.07692307692307693, 'support': 22}, 'accuracy': 0.8297872340425532, 'macro avg': {'precision': 0.5483576642335766, 'recall': 0.510122230710466, 'f1-score': 0.49158653846153844, 'support': 141}, 'weighted avg': {'precision': 0.7536108091318527, 'recall': 0.8297872340425532, 'f1-score': 0.77685147299509, 'support': 141}}}
PPP scores with cleaning: 

Outlier detection method: NoOutlierDetection, Outlier Detection Score: {'Precision': 0.43882978723404253, 'Recall': 0.625, 'F1-score': 0.5011792452830188, 'Accuracy': 0.6276595744680851}
Imputation method: MeanModeImputation, Imputation Score: {'Precision': 1.0, 'Recall': 1.0, 'F1-score': 1.0, 'Accuracy': 1.0, 'Mean Squared Error': 27686.443491879054}
Cleaner:

/home/rupali/.local/lib/python3.8/site-packages/sklearn/model_selection/_search.py:818: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  dtype=np.int)
/home/rupali/.local/lib/python3.8/site-packages/sklearn/ensemble/_gb.py:1352: DeprecationWarning: `np.object` is a deprecated alias for the builtin `object`. To silence this warning, use `object` by itself. Doing this will not modify any behavior and is safe. 
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  dtype=np.object)
/h

Classifier for col: DGN reached 0.6920252139717789


/home/rupali/.local/lib/python3.8/site-packages/sklearn/model_selection/_search.py:818: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  dtype=np.int)
/home/rupali/.local/lib/python3.8/site-packages/sklearn/ensemble/_gb.py:1352: DeprecationWarning: `np.object` is a deprecated alias for the builtin `object`. To silence this warning, use `object` by itself. Doing this will not modify any behavior and is safe. 
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  dtype=np.object)
/h

...

/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/rupali/.local/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/rupali/.local/lib/python3.8/site-packages/sklearn/linear_model/_base.py:295: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish


Outlier detection method: SklearnOutlierDetection, Outlier Detection Score: {'Precision': 0.7859247234247234, 'Recall': 0.7490631733664398, 'F1-score': 0.7412839811584151, 'Accuracy': 0.8723404255319149}
Imputation method: DatawigImputation, Imputation Score: {'Precision': 0.7368633139909736, 'Recall': 0.7479166666666667, 'F1-score': 0.7422503416917229, 'Accuracy': 0.9929078014184397, 'Mean Squared Error': 68.88301500285246}
Cleaner: (SklearnOutlierDetection, DatawigImputation): {'roc_auc_score': 0.6352177234530175, 'classification_report': {'F': {'precision': 0.8428571428571429, 'recall': 0.9915966386554622, 'f1-score': 0.9111969111969112, 'support': 119}, 'T': {'precision': 0.0, 'recall': 0.0, 'f1-score': 0.0, 'support': 22}, 'accuracy': 0.8368794326241135, 'macro avg': {'precision': 0.42142857142857143, 'recall': 0.4957983193277311, 'f1-score': 0.4555984555984556, 'support': 141}, 'weighted avg': {'precision': 0.7113475177304964, 'recall': 0.8368794326241135, 'f1-score': 0.76902434

/home/rupali/.local/lib/python3.8/site-packages/sklearn/ensemble/_bagging.py:314: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  elif isinstance(self.max_features, np.float):
/home/rupali/.local/lib/python3.8/site-packages/sklearn/ensemble/_base.py:179: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and 

/home/rupali/.local/lib/python3.8/site-packages/sklearn/ensemble/_bagging.py:314: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  elif isinstance(self.max_features, np.float):
/home/rupali/.local/lib/python3.8/site-packages/sklearn/ensemble/_base.py:179: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and 

Imputed 1 values in column DGN
Imputed 70 values in column PRE30
Imputed 91 values in column PRE4
Imputed 90 values in column PRE5
Imputed 31 values in column AGE

Best cleaning method:
Cleaning score: Cleaner: (PyODIsolationForestOutlierDetection, SklearnImputation): {'roc_auc_score': 0.7043544690603514, 'classification_report': {'F': {'precision': 0.8444444444444444, 'recall': 0.957983193277311, 'f1-score': 0.8976377952755905, 'support': 119}, 'T': {'precision': 0.16666666666666666, 'recall': 0.045454545454545456, 'f1-score': 0.07142857142857144, 'support': 22}, 'accuracy': 0.8156028368794326, 'macro avg': {'precision': 0.5055555555555555, 'recall': 0.5017188693659282, 'f1-score': 0.48453318335208095, 'support': 141}, 'weighted avg': {'precision': 0.7386918833727345, 'recall': 0.8156028368794326, 'f1-score': 0.7687257177959138, 'support': 141}}} 

Cleaning improved the overall score 





## Model Evaluation

### With learner and param_grid

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer

# preprocessing pipeline for numerical columns
transformer_numeric = Pipeline([
    ('imputer', SimpleImputer(strategy='constant', fill_value=0)),
    ('standard_scale', StandardScaler())
])

# preprocessing pipeline for categorical columns
transformer_categorical = Pipeline([
    ('imputer', SimpleImputer(strategy='constant', fill_value='__NA__')),
    ('one_hot_encode', OneHotEncoder(handle_unknown='ignore'))
])

# preprocessor
feature_transform = ColumnTransformer(transformers=[
    ('categorical_features', transformer_categorical, categorical_columns),
    ('numerical_features', transformer_numeric, numerical_columns)
])

## prediction pipeline: append classifier (learner) to the preprocessing pipeline
pipeline = Pipeline([
    ('features', feature_transform),
    ('learner', learner)
])

In [ ]:
from sklearn.model_selection import GridSearchCV

grid_search = GridSearchCV(pipeline, param_grid, scoring='roc_auc', cv=5, verbose=1, n_jobs=-1)
model = grid_search.fit(train_data, train_labels)

In [ ]:
y_pred = model.predict(test_data)

In [ ]:
from sklearn.metrics import roc_auc_score

roc_auc_score(test_labels, np.transpose(model.predict_proba(test_data))[1])

In [ ]:
model.predict_proba(test_data)

In [ ]:
from sklearn.metrics import classification_report

classification_report(test_labels, y_pred, output_dict=True)

### With Autogluon

In [ ]:
from autogluon.tabular import TabularPredictor

## training
train_data["class"] = train_labels

label = "class"

## folder to save trained models
#save_path = '/home/rupali/Documents/Master Thesis/jenga/autogluon_models/'

predictor = TabularPredictor(label=label).fit(train_data)

In [ ]:
## test on original data
y_pred_test = predictor.predict(test_data)
perf = predictor.evaluate_predictions(y_true=pd.Series(test_labels), y_pred=y_pred_test, auxiliary_metrics=True)

In [ ]:
## test on corrupted data
y_pred_corrupted = predictor.predict(df_corrupted)
perf = predictor.evaluate_predictions(y_true=pd.Series(test_labels), y_pred=y_pred_corrupted, auxiliary_metrics=True)

In [ ]:
## test on cleaned data
y_pred_cleaned = predictor.predict(df_cleaned)
perf = predictor.evaluate_predictions(y_true=pd.Series(test_labels), y_pred=y_pred_cleaned, auxiliary_metrics=True)

In [ ]:
## We can evaluate the performance of each individual trained model on our (labeled) test data
test_data["class"] = test_labels
predictor.leaderboard(test_data, silent=True)

In [ ]:
perf

In [ ]:
list(perf.items())[6][1]

In [ ]:
from sklearn.metrics import roc_auc_score

roc_auc_score(test_labels, np.transpose(predictor.predict_proba(test_data)).to_numpy()[1])

In [ ]:
perf = predictor.evaluate_predictions(y_true=pd.Series(test_labels), y_pred=y_pred_cleaned, auxiliary_metrics=False)
perf

## Undefined Model: Default setting: whole process

In [ ]:
from jenga.corruptions.generic import MissingValues, SwappedValues, CategoricalShift
from jenga.corruptions.numerical import Scaling, GaussianNoise

corruptions = [MissingValues, Scaling, GaussianNoise, CategoricalShift]
fraction = 0.5
num_repetitions = 5

In [ ]:
from jenga.cleaning.ppp import PipelinePerformancePrediction

ppp = PipelinePerformancePrediction(train_data, train_labels, test_data, test_labels, categorical_columns, numerical_columns)
ppp_model = ppp.fit_ppp(train_data)

## generate corrpted data
for _ in range(num_repetitions):
    df_corrupted, perturbations, cols_perturbed, summary_col_corrupt = ppp.get_corrupted(test_data, corruptions, fraction, num_repetitions)

In [ ]:
from jenga.cleaning.outlier_detection import NoOutlierDetection, PyODKNNOutlierDetection, PyODIsolationForestOutlierDetection, PyODPCAOutlierDetection, PyODCBLOFOutlierDetection, PyODSOSOutlierDetection
from jenga.cleaning.imputation import MeanModeImputation

cleaners = [
    (NoOutlierDetection, MeanModeImputation),
    (PyODKNNOutlierDetection, MeanModeImputation),
    (PyODIsolationForestOutlierDetection, MeanModeImputation),
    (PyODPCAOutlierDetection, MeanModeImputation),
    (PyODCBLOFOutlierDetection, MeanModeImputation),
    (PyODSOSOutlierDetection, MeanModeImputation)
]

In [ ]:
from jenga.cleaning.clean import Clean

categorical_precision_threshold=0.7
numerical_std_error_threshold=2.0

clean = Clean(train_data, df_corrupted, categorical_columns, numerical_columns, categorical_precision_threshold, numerical_std_error_threshold, ppp, ppp_model, cleaners)
df_outliers, df_cleaned, corrupted_score_ppp, best_cleaning_score, cleaner_scores_ppp, summary_cleaners = clean(train_data, test_data, df_corrupted, cols_perturbed)

## Try Cleaners

In [ ]:
from pyod.models.knn import KNN
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.impute import SimpleImputer
from sklearn.compose import ColumnTransformer

In [ ]:
## featurizers
def build_featurizers(columns):
    categorical_preprocessing = Pipeline([
        ('mark_missing', SimpleImputer(strategy='constant', fill_value='__NA__')),
        ('one_hot_encode', OneHotEncoder(handle_unknown='ignore'))
    ])

    numeric_preprocessing = Pipeline([
        ('mark_missing', SimpleImputer(strategy='constant', fill_value=0)),
    ])

    cat_cols = [c for c in categorical_columns if c in columns]
    num_cols = [c for c in numerical_columns if c in columns]
    
    feature_transformation = ColumnTransformer(transformers=[
        ('categorical_features', categorical_preprocessing, cat_cols),
        ('scaled_numeric', numeric_preprocessing, num_cols)
    ])

    return feature_transformation

### Pyod Single Column - features

In [ ]:
df_outliers = df_corrupted.copy(deep=True)
df_outliers

In [ ]:
predictors = {}

for col in categorical_columns + numerical_columns:
    predictors[col] = Pipeline(
        [('features', build_featurizers([col])),
         ('outlier_detector', KNN())
        ])
    
len(predictors)

In [ ]:
for col in categorical_columns + numerical_columns:
    predictors[col].fit(df_outliers)

In [ ]:
for col in categorical_columns + numerical_columns:
    df_outliers[col + "_outlier"] = predictors[col].predict(df_corrupted)

In [ ]:
df_outliers

### Pyod Multiple Columns - features

In [ ]:
df_outliers = df_corrupted.copy(deep=True)

In [ ]:
predictors = Pipeline(
    [('features', build_featurizers(numerical_columns + categorical_columns)),
     ('outlier_detector', KNN())
    ])
predictors.fit(df_outliers)

In [ ]:
outliers = predictors.predict(df_outliers)
outliers

### Categorical from train, numerical from pyod

In [ ]:
## single column based

In [ ]:
def cat_out_detect(df_train, df_corrupted):
    df_outliers = df_corrupted[categorical_columns].copy()
    
    for col in df_train.columns:
        if col in categorical_columns:
            vals_train_unique = df_train[col].unique()
            
            ## add a respective outlier col for each col
            df_outliers[col + "_outlier"] = ''
            
            for i in df_corrupted[col].index:
                if df_corrupted.loc[i, col] in vals_train_unique:
                    df_outliers.loc[i, col + "_outlier"] = 0
                else:
                    df_outliers.loc[i, col + "_outlier"] = 1
                    
    return df_outliers

In [ ]:
def num_out_detect(df_train, df_corrupted, pyod_model):
    df_outliers = df_corrupted[numerical_columns].copy()
    
    for col in df_train.columns:
        if col in numerical_columns:
            ## find indices of records with NaNs in col in df_corrupted
            nan_idx = df_corrupted[df_corrupted[col].isnull()].index
            non_nan_idx = df_corrupted.loc[set(df_corrupted.index) - set(nan_idx)].index
            
            ## pd series -> np column, needs to be 2D array
            ## taking only the non-NaN records in the corrupted data
            col_tr_arr = np.array(df_train[col]).reshape(-1,1)
            col_corr_arr = np.array(df_corrupted.loc[non_nan_idx][col]).reshape(-1,1)
            
            ## fit the dataset to the model
            model = pyod_model
            model.fit(col_tr_arr)
            
            ## predict raw anomaly score
            scores_pred = model.decision_function(col_corr_arr) * -1
            
            ## prediction of a datapoint category outlier or inlier
            y_pred = model.predict(col_corr_arr)
            
            ## add a respective outlier col for each col
            df_outliers[col + "_outlier"] = ''
            df_outliers.loc[non_nan_idx, col + "_outlier"] = y_pred ## 0: inlier, 1: outlier
            df_outliers.loc[nan_idx, col + "_outlier"] = 1
            
    return df_outliers

In [ ]:
from pyod.models.knn import KNN

pyod_model = KNN()
    
df_outliers_num = num_out_detect(train_data, df_corrupted, pyod_model)
df_outliers_cat = cat_out_detect(train_data, df_corrupted)

df_outliers = df_outliers_num.join(df_outliers_cat, how='inner')
df_outliers

In [ ]:
from pyod.models.pca import PCA

pyod_model = PCA() # n_components = min(n_samples, n_features) default  # n_selected_components = None
    
df_outliers_num = num_out_detect(train_data, df_corrupted, pyod_model)
df_outliers_cat = cat_out_detect(train_data, df_corrupted)

df_outliers = df_outliers_num.join(df_outliers_cat, how='inner')
df_outliers

In [ ]:
from pyod.models.cblof import CBLOF

pyod_model = CBLOF() # n_clusters = 8 default
    
df_outliers_num = num_out_detect(train_data, df_corrupted, pyod_model)
df_outliers_cat = cat_out_detect(train_data, df_corrupted)

df_outliers = df_outliers_num.join(df_outliers_cat, how='inner')
df_outliers

In [ ]:
from pyod.models.sos import SOS

pyod_model = SOS()
    
df_outliers_num = num_out_detect(train_data, df_corrupted, pyod_model)
df_outliers_cat = cat_out_detect(train_data, df_corrupted)

df_outliers = df_outliers_num.join(df_outliers_cat, how='inner')
df_outliers

### Sklearn

In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.ensemble import GradientBoostingClassifier, GradientBoostingRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import classification_report, precision_recall_curve

In [ ]:
df_outliers = df_corrupted.copy(deep=True)

In [ ]:
categorical_precision_threshold = 0.85
numeric_error_percentile = 0.9

predictors = {}
predictable_cols = []

In [ ]:
categorical_preprocessing = Pipeline([
    ('mark-missing', SimpleImputer(strategy='constant', fill_value='__NA__')),
    ('one_hot_encode', OneHotEncoder(handle_unknown='ignore'))
])

numeric_preprocessing = Pipeline([
    ('mark_missing', SimpleImputer(strategy='median')),
    ('scaling', StandardScaler())
])

In [ ]:
## cat to string

#### Categoric

In [ ]:
col = "V14"

In [ ]:
len(train_data[col].unique())

In [ ]:
feature_transform = ColumnTransformer(transformers=[
    ('categorical_features', categorical_preprocessing, list(set(categorical_columns) - {col})),
    ('numeric_features', numeric_preprocessing, numerical_columns)
])

In [ ]:
param_grid = {
    'learner__n_estimators': [10, 50, 100, 200],
}

In [ ]:
pipeline = Pipeline([
    ('features', feature_transform),
    ('learner', GradientBoostingClassifier())
])

In [ ]:
search = GridSearchCV(pipeline, param_grid, cv=2, verbose=0, n_jobs=-1)
predictors[col] = search.fit(train_data, train_data[col])

print(f'Classifier for col: {col} reached {search.best_score_}')

In [ ]:
train_data

In [ ]:
test_data

In [ ]:
## precision-recall curves for finding the likelihood thresholds for minimal precision
predictors[col].thresholds = {}
probas = predictors[col].predict_proba(test_data)

for label_idx, label in enumerate(predictors[col].classes_):
    prec, rec, threshold = precision_recall_curve(test_data[col]==label, probas[:,label_idx], pos_label=True)
    prec = prec.tolist(); rec = rec.tolist(); threshold = threshold.tolist()
    threshold_for_min_prec = np.array([elem >= categorical_precision_threshold for elem in prec]).nonzero()[0][0] - 1
    predictors[col].thresholds[label] = threshold_for_min_prec

In [ ]:
##############################

In [ ]:
threshold

In [ ]:
np.array([elem >= categorical_precision_threshold for elem in prec]).nonzero()[0][0] - 1

In [ ]:
threshold[36]

In [ ]:
len(threshold)

In [ ]:
##############################

In [ ]:
predictors[col].thresholds

In [ ]:
## outlier detection

In [ ]:
y_pred = predictors[col].predict(df_corrupted)
y_proba = predictors[col].predict_proba(df_corrupted)

for label_idx, label in enumerate(predictors[col].classes_):
    precision_pred = predictors[col].thresholds[label] <= y_proba[:,label_idx]
    outliers = precision_pred & (df_corrupted[col] != y_pred)

In [ ]:
outliers

In [ ]:
## find indices of records with NaNs in col in df_corrupted
nan_idx = df_corrupted[df_corrupted[col].isnull()].index
non_nan_idx = df_corrupted.loc[set(df_corrupted.index) - set(nan_idx)].index
        
## add a respective outlier col for each col
df_outliers[col + "_outlier"] = ''
df_outliers.loc[non_nan_idx, col + "_outlier"] = outliers.astype('int') ## 0: inlier, 1: outlier
df_outliers.loc[nan_idx, col + "_outlier"] = 1

In [ ]:
df_outliers

In [ ]:
for i in df_outliers.index:
    if df_outliers.loc[i, col + "_outlier"] == 1:
        df_outliers.loc[i, col] = np.nan

In [ ]:
print(f'Column {col} contained {len(nan_idx)} nans before, now {df_outliers[col].isnull().sum()}')

In [ ]:
## imputation

In [ ]:
prior_missing = df_outliers[col].isnull().sum()

if prior_missing > 0:
    df_outliers.loc[df_outliers[col].isnull(), col] = predictors[col].predict(df_outliers[df_outliers[col].isnull()])
    
print(f'Imputed {prior_missing} values in column {col}')

#### Numeric

In [ ]:
col = "V16"

In [ ]:
feature_transform = ColumnTransformer(transformers=[
    ('categorical_features', categorical_preprocessing, categorical_columns),
    ('numeric_features', numeric_preprocessing, list(set(numerical_columns) - {col}))
])

In [ ]:
param_grid = {
    'learner__n_estimators': [10, 50, 100],
}

In [ ]:
predictors[col] = {}

for perc_name, percentile, in zip(['lower', 'median', 'upper'], [1.0 - numeric_error_percentile, 0.5, numeric_error_percentile]):
    pipeline = Pipeline([
        ('features', feature_transform),
        ('learner', GradientBoostingRegressor(loss='quantile', alpha=percentile))
    ])
    
    search = GridSearchCV(pipeline, param_grid, cv=2, verbose=0, n_jobs=-1)
    predictors[col][perc_name] = search.fit(train_data, train_data[col])
    print(f'Regressor for col: {col}/{perc_name} reached {search.best_score_}')

In [ ]:
## outlier detection

In [ ]:
lower_percentile = predictors[col]['lower'].predict(df_corrupted)
upper_percentile = predictors[col]['upper'].predict(df_corrupted)

outliers = (df_corrupted[col] < lower_percentile) | (df_corrupted[col] > upper_percentile)

In [ ]:
outliers

In [ ]:
num_nans = df_outliers[col].isnull().sum()
df_outliers.loc[outliers, col] = np.nan

In [ ]:
## find indices of records with NaNs in col in df_corrupted
nan_idx = df_corrupted[df_corrupted[col].isnull()].index
non_nan_idx = df_corrupted.loc[set(df_corrupted.index) - set(nan_idx)].index
        
## add a respective outlier col for each col
df_outliers[col + "_outlier"] = ''
df_outliers.loc[non_nan_idx, col + "_outlier"] = outliers.astype('int') ## 0: inlier, 1: outlier
df_outliers.loc[nan_idx, col + "_outlier"] = 1

In [ ]:
df_outliers

In [ ]:
for i in df_outliers.index:
    if df_outliers.loc[i, col + "_outlier"] == 1:
        df_outliers.loc[i, col] = np.nan

In [ ]:
print(f'Column {col} contained {len(nan_idx)} nans before, now {df_outliers[col].isnull().sum()}')

In [ ]:
## imputation

In [ ]:
prior_missing = df_outliers[col].isnull().sum()

if prior_missing > 0:
    df_outliers.loc[df_outliers[col].isnull(), col] = predictors[col]['median'].predict(df_outliers[df_outliers[col].isnull()])
    
print(f'Imputed {prior_missing} values in column {col}')

#### Together

In [ ]:
for col in categorical_columns + numerical_columns:
    if col in categorical_columns:
        if len(train_data[col].unique()) > 1:
            feature_transform = ColumnTransformer(transformers=[
                ('categorical_features', categorical_preprocessing, list(set(categorical_columns) - {col})),
                ('numeric_features', numeric_preprocessing, numerical_columns)
            ])

            param_grid = {
                'learner__n_estimators': [10, 50, 100, 200],
            }

            pipeline = Pipeline([
                ('features', feature_transform),
                ('learner', GradientBoostingClassifier())
            ])

            search = GridSearchCV(pipeline, param_grid, cv=2, verbose=0, n_jobs=-1)
            predictors[col] = search.fit(train_data, train_data[col])

            print(f'Classifier for col: {col} reached {search.best_score_}')

            ## precision-recall curves for finding the likelihood thresholds for minimal precision
            predictors[col].thresholds = {}
            probas = predictors[col].predict_proba(test_data)

            for label_idx, label in enumerate(predictors[col].classes_):
                prec, rec, threshold = precision_recall_curve(test_data[col]==label, probas[:,label_idx], pos_label=True)
                prec = prec.tolist(); rec = rec.tolist(); threshold = threshold.tolist()
                threshold_for_min_prec = np.array([elem >= categorical_precision_threshold for elem in prec]).nonzero()[0][0] - 1
                predictors[col].thresholds[label] = threshold_for_min_prec

    elif col in numerical_columns:
        feature_transform = ColumnTransformer(transformers=[
            ('categorical_features', categorical_preprocessing, categorical_columns),
            ('numeric_features', numeric_preprocessing, list(set(numerical_columns) - {col}))
        ])
        
        param_grid = {
            'learner__n_estimators': [10, 50, 100],
        }
        
        predictors[col] = {}
        
        for perc_name, percentile, in zip(['lower', 'median', 'upper'], [1.0 - numeric_error_percentile, 0.5, numeric_error_percentile]):
            pipeline = Pipeline([
                ('features', feature_transform),
                ('learner', GradientBoostingRegressor(loss='quantile', alpha=percentile))
            ])
            
            search = GridSearchCV(pipeline, param_grid, cv=2, verbose=0, n_jobs=-1)
            predictors[col][perc_name] = search.fit(train_data, train_data[col])
            
            print(f'Regressor for col: {col}/{perc_name} reached {search.best_score_}')

In [ ]:
predictors.keys()

In [ ]:
## outlier detection and removal

In [ ]:
for col in categorical_columns + numerical_columns:
    if col in categorical_columns:
        if col in predictors.keys():
            y_pred = predictors[col].predict(df_corrupted)
            y_proba = predictors[col].predict_proba(df_corrupted)

            for label_idx, label in enumerate(predictors[col].classes_):
                precision_pred = predictors[col].thresholds[label] <= y_proba[:,label_idx]
                outliers = precision_pred & (df_corrupted[col] != y_pred)
            
    elif col in numerical_columns:
        lower_percentile = predictors[col]['lower'].predict(df_corrupted)
        upper_percentile = predictors[col]['upper'].predict(df_corrupted)
        outliers = (df_corrupted[col] < lower_percentile) | (df_corrupted[col] > upper_percentile)
        
    ## find indices of records with NaNs in col in df_corrupted
    nan_idx = df_corrupted[df_corrupted[col].isnull()].index
    non_nan_idx = df_corrupted.loc[set(df_corrupted.index) - set(nan_idx)].index
    
    ## add a respective outlier col for each col
    df_outliers[col + "_outlier"] = ''
    df_outliers.loc[non_nan_idx, col + "_outlier"] = outliers.astype('int') ## 0: inlier, 1: outlier
    df_outliers.loc[nan_idx, col + "_outlier"] = 1
    
    for i in df_outliers.index:
        if df_outliers.loc[i, col + "_outlier"] == 1:
            df_outliers.loc[i, col] = np.nan
    
    print(f'Column {col} contained {len(nan_idx)} nans before, now {df_outliers[col].isnull().sum()}')

In [ ]:
## imputation

In [ ]:
df_cleaned = df_outliers[df_corrupted.columns].copy(deep=True)

In [ ]:
for col in categorical_columns + numerical_columns:
    prior_missing = df_cleaned[col].isnull().sum()
    
    if prior_missing > 0:
        if col in categorical_columns:
            df_cleaned.loc[df_cleaned[col].isnull(), col] = predictors[col].predict(df_cleaned[df_cleaned[col].isnull()])
        elif col in numerical_columns:
            df_cleaned.loc[df_cleaned[col].isnull(), col] = predictors[col]['median'].predict(df_cleaned[df_cleaned[col].isnull()])
        
        print(f'Imputed {prior_missing} values in column {col}')

## Swapping

In [ ]:
## Swapping between a categoric and numeric variable messes up the categories of the categoric variable, and there
## are issues while comparing the values inside the same column
## Here, I am finding all the numeric values in the categoric columns, that came after using the SwappedValues corruption
## and repacing them with NaNs, they will later be imputed.

In [ ]:
test_data

In [ ]:
df_corrupted

In [ ]:
df_corrupted.index[np.where(df_corrupted.applymap(np.isreal)["Chest_pain_type"] == True)]

In [ ]:
df_corrupted.loc[df_corrupted.index[np.where(df_corrupted.applymap(np.isreal)["Chest_pain_type"] == True)]]

In [ ]:
for col in categorical_columns:
    idx_to_nan = df_corrupted.index[np.where(df_corrupted.applymap(np.isreal)[col] == True)]
    if len(idx_to_nan) != 0:
        df_corrupted.loc[idx_to_nan, col] = np.nan

In [ ]:
df_corrupted["Chest_pain_type"]

In [ ]:
numerical_columns

In [ ]:
df_corrupted[['Age', 'Trestbps', 'Cholesterol', 'Max_heart_rate', 'Oldpeak']]

In [ ]:
df_corrupted["Age"].isalpha()

## Datawig Imputation

In [ ]:
!pip3 install datawig

In [ ]:
import datawig

In [ ]:
df_imputed = df_outliers[df_corrupted.columns].copy(deep=True)

In [ ]:
for col in categorical_columns + numerical_columns:
    output_col = col
    input_cols = list(set(train_data.columns) - set([output_col]))
    
    print(f'Fitting model for column: {col}')
    model = datawig.SimpleImputer(input_cols, output_col, 'imputer_model')
    model.fit(train_data)
    
    df_imputed = model.predict(df_imputed)
    df_imputed[col].fillna(df_imputed[col + '_imputed'], inplace=True)
    df_imputed = df_imputed[df_corrupted.columns]

In [ ]:
df_imputed

In [ ]:
df_outliers